In [1]:
import datetime as dt
import math

import matplotlib.pyplot as plt
import mplfinance as mpf
import numpy as np
import pandas as pd
import pandas_market_calendars as mcal
import plotly.graph_objects as go
import polars as pl
from dash import Dash, dcc, html
from plotly.subplots import make_subplots

nse = mcal.get_calendar("NSE")

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

pd.options.display.float_format = "{:.4f}".format

import sys

sys.path.append("..")
# from tooling.enums import AssetClass, Index, Spot, StrikeSpread
# from tooling.fetch import fetch_option_data, fetch_spot_data
# from tooling.filter import find_atm, option_tool

from fetching_from_local_db.enums import AssetClass, Index, StrikeSpread
from fetching_from_local_db.fetch_from_db import (
    _fetch_batch,
    fetch_data,
    fetch_spot_data,
)

In [2]:
async def get_expiry(f_today):

    if (f_today <= dt.date(2024, 1, 25)) and (f_today >= dt.date(2024, 1, 18)):
        f_expiry = dt.date(2024, 1, 25)
    elif (f_today <= dt.date(2024, 1, 31)) and (f_today >= dt.date(2024, 1, 26)):
        f_expiry = dt.date(2024, 1, 31)
    elif (f_today <= dt.date(2024, 2, 22)) and (f_today >= dt.date(2024, 2, 29)):
        f_expiry = dt.date(2024, 2, 29)
    elif (f_today <= dt.date(2024, 3, 25)) and (f_today >= dt.date(2024, 3, 27)):
        f_expiry = dt.date(2024, 2, 27)
    elif f_today < dt.date(2023, 9, 1):
        days_to_thursday = (3 - f_today.weekday()) % 7
        nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
        f_expiry = nearest_thursday
        if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
            f_expiry = nearest_thursday - dt.timedelta(days=1)
    elif f_today >= dt.date(2023, 9, 1):
        if f_today.day < 24:
            days_to_wednesday = (2 - f_today.weekday()) % 7
            nearest_wednesday = f_today + dt.timedelta(days=days_to_wednesday)
            f_expiry = nearest_wednesday
            if nse.valid_days(
                start_date=nearest_wednesday, end_date=nearest_wednesday
            ).empty:
                f_expiry = nearest_wednesday - dt.timedelta(days=1)
        else:
            days_to_thursday = (3 - f_today.weekday()) % 7
            nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
            f_expiry = nearest_thursday
            if nse.valid_days(
                start_date=nearest_thursday, end_date=nearest_thursday
            ).empty:
                f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


async def get_expiry_finnifty(f_today):

    days_to_thursday = (1 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


async def get_expiry_nifty(f_today):

    days_to_thursday = (3 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


async def get_expiry_midcpnifty(f_today):

    days_to_thursday = (0 - f_today.weekday()) % 7
    nearest_thursday = f_today + dt.timedelta(days=days_to_thursday)
    f_expiry = nearest_thursday
    if nse.valid_days(start_date=nearest_thursday, end_date=nearest_thursday).empty:
        f_expiry = nearest_thursday - dt.timedelta(days=1)
    return f_expiry


import datetime as dt


async def get_monthly_expiry_nifty(input_date):
    # Get the last day of the current month
    current_month_last_day = (
        input_date.replace(day=28) + dt.timedelta(days=4)
    ).replace(day=1) - dt.timedelta(days=1)

    # Find the last Thursday of the current month
    last_thursday_current_month = current_month_last_day - dt.timedelta(
        days=(current_month_last_day.weekday() - 3) % 7
    )

    # Check if the current date is less than the last Thursday of the current month
    if input_date < last_thursday_current_month:
        last_thursday = last_thursday_current_month
    else:
        # If the current date has passed the last Thursday, find the last Thursday of the next month
        next_month = (input_date.month % 12) + 1
        next_month_year = input_date.year if next_month > 1 else input_date.year + 1

        # Get the last day of the next month (considering February correctly)
        if next_month == 2:  # February
            if next_month_year % 4 == 0 and (
                next_month_year % 100 != 0 or next_month_year % 400 == 0
            ):
                last_day_of_next_month = 29  # Leap year
            else:
                last_day_of_next_month = 28  # Non-leap year
        else:
            # Calculate the last day of the next month
            last_day_of_next_month = (
                dt.date(next_month_year, next_month, 1) + dt.timedelta(days=31)
            ).replace(day=1) - dt.timedelta(days=1)
            last_day_of_next_month = (
                last_day_of_next_month.day
            )  # Extract the day as an integer

        # Create a date for the last day of the next month
        last_day_of_next_month_date = dt.date(
            next_month_year, next_month, last_day_of_next_month
        )

        # Find the last Thursday of the next month
        last_thursday = last_day_of_next_month_date - dt.timedelta(
            days=(last_day_of_next_month_date.weekday() - 3) % 7
        )

    # Validate if the last Thursday is a trading day
    if nse.valid_days(start_date=last_thursday, end_date=last_thursday).empty:
        # If it's a holiday, find the previous valid trading day
        last_thursday -= dt.timedelta(days=1)
        while nse.valid_days(start_date=last_thursday, end_date=last_thursday).empty:
            last_thursday -= dt.timedelta(days=1)

    return last_thursday


async def get_option_contract_name(symbol, strike, expiry, opt_type):
    temp = "0"
    mth = expiry.month

    if (expiry + dt.timedelta(days=7)).month != expiry.month:
        date_string = expiry.strftime("%y%b").upper()
        return f"{symbol}{date_string}{strike}{opt_type}"
    else:
        if expiry.day <= 9:
            date_string = f"{expiry.year - 2000}{mth}{temp}{expiry.day}"
        else:
            date_string = f"{expiry.year - 2000}{mth}{expiry.day}"
        return f"{symbol}{date_string}{strike}{opt_type}"

In [3]:
# bnf_pandas = pd.read_csv("../data/bnf_min.csv")
bnf_pandas = pd.read_csv("../data/nifty_min.csv")
# bnf_pandas = pd.read_csv("../data/fin_min.csv")
# bnf_pandas = pd.read_csv("../data/midcp_min.csv")
# bnf_pandas = pd.read_csv("../data/sensex_min.csv")
# bnf_pandas = pd.read_csv("../data/bankex_min.csv")

In [4]:
bnf_pandas.columns = ['index', 'datetime', 'o', 'h', 'l', 'c', 'v']
bnf_pandas.tail()

index             datetime          o          h          l  \
777613  nifty  2025-05-30 15:25:00 24741.4000 24742.7000 24740.5000   
777614  nifty  2025-05-30 15:26:00 24742.2500 24746.2000 24740.3000   
777615  nifty  2025-05-30 15:27:00 24741.0500 24749.0500 24739.5000   
777616  nifty  2025-05-30 15:28:00 24746.5500 24746.8000 24731.1000   
777617  nifty  2025-05-30 15:29:00 24743.6000 24749.3000 24731.8500   

                c  v  
777613 24741.7000  0  
777614 24740.3000  0  
777615 24747.1500  0  
777616 24745.2500  0  
777617 24736.6500  0

In [5]:
# If Stocks Data ...
bnf_pandas["datetime"] = pd.to_datetime(bnf_pandas["datetime"])
bnf_pandas["datetime"] = bnf_pandas["datetime"].dt.tz_localize(None)
bnf_pandas = bnf_pandas[bnf_pandas["datetime"].dt.year >= 2017]
# bnf_pandas.drop(columns=["time"], inplace=True)
# bnf_pandas

In [6]:
bnf = pl.DataFrame(bnf_pandas)
print(type(bnf))
# bnf

<class 'polars.dataframe.frame.DataFrame'>


In [7]:
bnf = bnf.with_columns([pl.col("datetime").alias("index")]).drop("datetime")
bnf = bnf.with_columns(pl.col("index").alias("datetime"))

In [8]:
# bnf = bnf.rename({"open": "o", "high": "h", "low": "l", "close": "c", "volume": "v"})

In [9]:
def resample(data, timeframe, offset=None):
    agg_list = [
        pl.col("o").first().alias("o"),
        pl.col("h").max().alias("h"),
        pl.col("l").min().alias("l"),
        pl.col("c").last().alias("c"),
    ]
    if timeframe == '10m':
        offset = '5m'
    if "v" in data.columns:
        agg_list.append(pl.col("v").sum().alias("v"))
    return (
        data.set_sorted("datetime")
        .group_by_dynamic(
            index_column="datetime",
            every=timeframe,
            period=timeframe,
            label="left",
            offset=offset,
        )
        .agg(agg_list)
    )


In [10]:
# def generate_signals(df, n=5):
#     import numpy as np
#     import pandas as pd

#     # Ensure required columns are present
#     required_cols = {'o', 'h', 'l', 'c', 'datetime'}
#     if not required_cols.issubset(df.columns):
#         raise ValueError(f"DataFrame must contain columns: {required_cols}")
    
#     # Ensure datetime is in datetime format
#     if not np.issubdtype(df['datetime'].dtype, np.datetime64):
#         df['datetime'] = pd.to_datetime(df['datetime'])
    
#     # Calculate the low of the previous n candles
#     df['Prev_N_Low'] = df['l'].rolling(window=n).min().shift(1)
    
#     # Generate sell signal
#     df['Sell Signal'] = df['c'] < df['Prev_N_Low']
    
#     # Drop intermediate columns if not needed
#     df.drop(columns=['Prev_N_Low'], inplace=True, errors='ignore')
    
#     return df


In [11]:
# # USING SMA LOW for ENTRY
# def generate_signals(df, st_num=3, ema=5, pct=0.9):
#     """
#     Calculate signals for reversal selling strategy with SMA-based condition.
    
#     Parameters:
#     df (pd.DataFrame): Input DataFrame with columns 'datetime', 'o', 'h', 'l', 'c', and optionally 'v'.
#     st_num (int): Period for short-term SMA and low calculation.
#     ema (int): Period for EMA calculation.
#     pct (float): Percentage threshold for high price comparison.
    
#     Returns:
#     pd.DataFrame: DataFrame with additional columns 'Reversal Sell Signal' and tracking indicators.
#     """
#     # Ensure the DataFrame has the required columns
#     required_columns = {'datetime', 'h', 'l', 'c'}
#     if not required_columns.issubset(df.columns):
#         raise ValueError(f"Input DataFrame must contain columns: {required_columns}")
    
#     # Calculate short-term SMA of the lows
#     df['SMA_Low'] = df['l'].rolling(window=st_num).mean().shift(1)
    
#     # Calculate a very short-term EMA (e.g., 5-period)
#     df['EMA_5'] = df['c'].ewm(span=ema, adjust=False).mean()
    
#     # Calculate daily high till now
#     df['daily_high_till_now'] = df.groupby(df['datetime'].dt.date)['h'].cummax()
    
#     # Define Reversal Sell Signal
#     df['Sell Signal'] = (
#         (df['h'] > (pct * df['daily_high_till_now'].shift(1))) &  # Price is near or above the daily high
#         (df['c'] < df['SMA_Low'])  # Close below SMA of the lows
#     ).astype(int)
    
#     return df


In [12]:
def generate_signals(df, st_num=3, ema=5, pct=0.9):
    """
    Calculate signals for reversal selling strategy.
    
    Parameters:
    df (pd.DataFrame): Input DataFrame with columns 'datetime', 'o', 'h', 'l', 'c', and optionally 'v'.
    
    Returns:
    pd.DataFrame: DataFrame with additional columns 'Reversal Sell Signal' and tracking indicators.
    """
    # Ensure the DataFrame has the required columns
    required_columns = {'datetime', 'h', 'l', 'c'}
    if not required_columns.issubset(df.columns):
        raise ValueError(f"Input DataFrame must contain columns: {required_columns}")
    
    # Calculate a 3-period high (short-term high)
    df['short_term_low'] = df['l'].rolling(window=st_num).min().shift(1)

    # Calculate a very short-term EMA (e.g., 5-period)
    # df['EMA_5'] = df['c'].ewm(span=ema, adjust=False).mean()
    
    # Calculate daily high till now
    df['daily_high_till_now'] = df.groupby(df['datetime'].dt.date)['h'].cummax()
    
    # Define Reversal Sell Signal
    # df['Sell Signal'] = (
    #     (df['h'] > (pct*df['daily_high_till_now'].shift(1))) &  # Price is near or above the daily high
    #     (df['c'] < df['short_term_low']) &  # Closing below the short-term high (early weakness)
    #     (df['c'] < df['EMA_5'])  # Close below very short-term EMA for confirmation
    # ).astype(int)
    df['Sell Signal'] = (
        (df['h'] > (pct*df['daily_high_till_now'].shift(1))) &  # Price is near or above the daily high
        (df['c'] < df['short_term_low'])).astype(int)
    
    return df


In [13]:
data = bnf_pandas.copy()
# data['datetime'] = pd.to_datetime(data['datetime'].dt.date)
print(data["datetime"].tail())
trading_days_set = set(data["datetime"].dt.date)
# sorted(trading_days_set)

777613   2025-05-30 15:25:00
777614   2025-05-30 15:26:00
777615   2025-05-30 15:27:00
777616   2025-05-30 15:28:00
777617   2025-05-30 15:29:00
Name: datetime, dtype: datetime64[ns]


In [14]:
# GLOBAL VARIABLES

INSTRUMENT = "NIFTY"
INDEX = "nifty"
INDEX_MROUND = 50
# INDEX_MROUND=100

# INSTRUMENT = "NIFTY"
# INDEX = "nifty"
# INDEX_MROUND=50

PORTFOLIO_VALUE = 1_00_00_000
INDEX_LEV = 8
RPT_CE = 0.03
RPT_PE = 0.03
SLIPPAGE = 0.01
MAX_MARGIN = 250
TF = "10m"

# SIGNAL_MA = 20
# NUM_OF_CANDELS = 1
# T_MA=20
# TARGET=100

In [15]:
bnf = resample(bnf, TF)
data = bnf.to_pandas()
data.tail()
# data[['MA','signal_spot']]=MA(data,200)
# data[data['signal_spot']==1].head(50)
# bnf
# data.tail(50)
# data[data['datetime'].dt.date == dt.date(2024, 4, 29)]

datetime          o          h          l          c  v
78802 2025-05-30 14:45:00 24770.1000 24778.5500 24758.3000 24771.7000  0
78803 2025-05-30 14:55:00 24773.3000 24784.1000 24729.8000 24739.5000  0
78804 2025-05-30 15:05:00 24739.0000 24761.4500 24736.6000 24751.6500  0
78805 2025-05-30 15:15:00 24751.6500 24757.1500 24740.6000 24741.7500  0
78806 2025-05-30 15:25:00 24741.4000 24749.3000 24731.1000 24736.6500  0

In [31]:
async def ce_trade(data, st_high, ema, pct, start_date, end_date):
    df = data.copy()

    # start_date = dt.date(2025, 5, 9)
    # end_date = dt.date(2025, 5, 31)

    current_date = start_date

    combined_trades = pd.DataFrame()
    total_trades = pd.DataFrame()
    time_of_day = dt.time(9, 15)
    trade_book = []
    ce_lowest_low = float("inf")
    ce_highest_high = float("-inf")
    entry_rsi = 0

    while current_date < end_date:
        print(f'CE : {current_date}')
        entry = 0
        initial_sl = 0
        exit = 0
        in_ce_trade = False
        in_pe_trade = False
        # signal_exist=False

        points_captured = 0
        remark = ""
        trailing_active = False
        tsl = 0
        stop_trading = False
        is_gap_ce_sl = False
        previous_ce_sl_hit = False
        current_date_increament_flag = False
        # tsl_high = 0

        starting_time = dt.time(9, 15)

        ending_time = dt.time(15, 30)

        if not in_ce_trade and current_date in trading_days_set:

            ce_search_datetime = dt.datetime.combine(current_date, time_of_day)
            # print(f'current date : {ce_search_datetime}')

            spot_open = df.loc[df["datetime"] >= ce_search_datetime, "o"].iloc[0]
            print(f'spot open : {spot_open}')
            # spot_atm = int(round(spot_open / INDEX_MROUND) * INDEX_MROUND)
            spot_atm = int(
                math.ceil(spot_open / INDEX_MROUND) * INDEX_MROUND
            )  ##ROUNDS TO NEAREST 500 OTM
            # print(f'spot atm : {spot_atm}')
            # nearest_expiry = await get_expiry(current_date)
            nearest_expiry = await get_expiry_nifty(current_date)
            # if current_date== nearest_expiry:
            #     next_expiry_passing_value = current_date + dt.timedelta(days=1)
            #     nearest_expiry = await get_expiry_nifty( next_expiry_passing_value)
            # print(f'passing date for expry : {current_date}')
            # nearest_expiry = await get_monthly_expiry_nifty(current_date)
            # print(f'nearest expiry{nearest_expiry}')
            selected_strike_ce = spot_atm
            print(f'selected strike CE : {selected_strike_ce}')
            ce_df = await fetch_data(
                index=INDEX,
                start_date=nearest_expiry - dt.timedelta(days=7),
                start_time=starting_time,
                end_date=nearest_expiry,
                end_time=ending_time,
                strike=selected_strike_ce,
                asset_class="C",
                expiry=nearest_expiry,
            )
            print(ce_df)
            if ce_df is not None and not isinstance(ce_df, str):
                # print('new data fetched CE')
                data_ce = True
                ce_df = ce_df.select(["datetime", "o", "h", "l", "c", "v"])
                ce_df = resample(ce_df, TF)
                ce_df_pandas = ce_df.to_pandas()
                ce_df = generate_signals(ce_df_pandas, st_high, ema, pct)
                # ce_df = calculate_signals(ce_df_pandas)
                print(ce_df.to_string())
            else:
                data_ce = False
                current_date += dt.timedelta(days=1)
                continue

            if data_ce:

                for i in range(0, len(ce_df)):
                    current_candle = ce_df.iloc[i]
                    current_candle_open = ce_df.iloc[i]["o"]
                    current_candle_high = ce_df.iloc[i]["h"]
                    current_candle_low = ce_df.iloc[i]["l"]
                    current_candle_close = ce_df.iloc[i]["c"]

                    previous_candle_low = ce_df.iloc[i - 1]["l"]
                    previous_candle_close = ce_df.iloc[i - 1]["c"]
                    

                    expiry = nearest_expiry
                    strike = selected_strike_ce
                    asset_class = "C"
                    # print(ce_df.iloc[i])

                    signal = ce_df.iloc[i - 1]["Sell Signal"]
                    # candle_condition = (ce_df.iloc[i-1]['daily_high_till_now'] - previous_candle_close) > 10

                    if ce_df.iloc[i]["datetime"] >= ce_search_datetime:


                        if (
                            not previous_ce_sl_hit
                            and not in_ce_trade
                            and signal
                            # and current_candle_low < previous_candle_low
                            and ce_df.iloc[i]["datetime"].time() > time_of_day
                            and (
                                (nearest_expiry - ce_df.iloc[i]["datetime"].date()).days
                                >= 0
                                and (
                                    nearest_expiry - ce_df.iloc[i]["datetime"].date()
                                ).days
                                < 8
                            )
                            and ce_df.iloc[i]["datetime"].time() < dt.time(15, 25)
                            # and candle_condition
                        ):
                            # print(ce_df.iloc[i-1])
                            # print(f'entry found {previous_candle_low}')
                            # print(f'entry datetime {ce_df.iloc[i]["datetime"]}')
                            
                            # today_data = ce_df[ce_df['datetime'].dt.date == current_candle['datetime'].date()]
                            # day_high = today_data.iloc[0 : i-1]['h'].max()
                            # print(today_data.to_string())
                            
                            entry = current_candle_open
                            entry_date = ce_df.iloc[i-1]["datetime"].date()
                            entry_time = ce_df.iloc[i-1]["datetime"].time()
                            # initial_sl = ce_df.iloc[i - SL_CANDLES_NUM : i]["h"].max()
                            # initial_sl = day_high
                            initial_sl = ce_df.iloc[i-1]['daily_high_till_now']
                            in_ce_trade = True
                            ce_lowest_low = float("inf")
                            ce_highest_high = float("-inf")
                            # print(f'initial SL : {initial_sl}')
                            # entry_rsi = ce_df.iloc[i-1]['RSI']

                            qty = RPT_CE * PORTFOLIO_VALUE / (initial_sl - entry)
                            if (
                                (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                            ) * 100 > MAX_MARGIN:
                                qty = PORTFOLIO_VALUE * INDEX_LEV / strike * (MAX_MARGIN / 100)

                            # print(f'qty : {qty}')

                        # While in trade, track the highest high and lowest low
                        if in_ce_trade:
                            # Track the highest high
                            ce_highest_high = max(ce_highest_high, current_candle_high)

                            # Track the lowest low
                            ce_lowest_low = min(ce_lowest_low, current_candle_low)

                            # if all(
                            #     ce_df.loc[i - j, "h"] <= ce_df.loc[i - fractal_num, "h"]
                            #     for j in range(0, ((fractal_num * 2) + 1))
                            # ):
                            #     tsl_high = ce_df.loc[i - fractal_num, "h"]

                        if (
                            in_ce_trade
                            and ce_df.iloc[i]["datetime"].time() == dt.time(9, 15)
                            and current_candle_open > initial_sl
                        ):

                            # print(ce_df.iloc[i])
                            # print(f'GAP sl hit {initial_sl}')
                            # print(f'GAP sl datetime {ce_df.iloc[i]["datetime"]}')
                            exit = current_candle_close
                            in_ce_trade = False
                            stop_trading = False
                            previous_ce_sl_hit = True
                            is_gap_ce_sl = False
                            points_captured = entry - exit
                            exit_time = ce_df.iloc[i]["datetime"].time()
                            slippage = SLIPPAGE * (entry + exit)
                            pnl = qty * (points_captured - slippage)
                            remark = "Gap SL hit"
                            weekday_int = entry_date.weekday()
                            weekday_name = [
                                "Monday",
                                "Tuesday",
                                "Wednesday",
                                "Thursday",
                                "Friday",
                                "Saturday",
                                "Sunday",
                            ][weekday_int]
                            trade = {
                                "date": entry_date,
                                "day": weekday_name,
                                "expiry": expiry,
                                "DTE": (nearest_expiry - entry_date).days,
                                # 'atm' : atm,
                                # 'scrip' : index ,
                                "strike": strike,
                                "type": asset_class,
                                "Entry Price": entry,
                                "Entry Time": entry_time,
                                "initial sl": initial_sl,
                                # "TSL": tsl_high,
                                # 'OTM Entry' : otm_entry,
                                "Exit Price": exit,
                                "Exit date": ce_df.iloc[i]["datetime"].date(),
                                "Exit Time": exit_time,
                                'RSI on Entry': entry_rsi,
                                # 'OTM EXIT ' : otm_exit,
                                "Remark": remark,
                                "Points Captured": points_captured,
                                "Slippage": slippage,
                                # 'OTM cost' : otm_exit-otm_entry,
                                "Qty": qty,
                                "PnL": pnl,
                                "ROI%": (pnl / PORTFOLIO_VALUE) * 100,
                                "Trade Year": ce_df.iloc[i]["datetime"].year,
                                "Trade Month": ce_df.iloc[i]["datetime"].month,
                                "Highest High": ce_highest_high,  # Add highest high to trade data
                                "Lowest Low": ce_lowest_low,  # Add lowest low to trade data
                                "Max ROI%": (
                                    (qty * (entry - ce_lowest_low)) / PORTFOLIO_VALUE
                                )
                                * 100,
                                "Margin": (
                                    (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                                )
                                * 100,
                            }
                            # print(trade)
                            trade_book.append(trade)
                            # tsl_high = 0
                            points_captured = 0
                            current_date = ce_df.iloc[i]["datetime"].date()
                            current_date_increament_flag = True
                            time_of_day = ce_df.iloc[i]["datetime"].time()
                            # print(f'current date changed to : {current_date} and time to {time_of_day}')
                            break

                        if in_ce_trade and current_candle_high > initial_sl:
                            # print(ce_df.iloc[i])
                            # print(f'initial sl hit {initial_sl}')
                            # print(f'initial sl datetime {ce_df.iloc[i]["datetime"]}')
                            exit = initial_sl
                            otm_datetime = ce_df.iloc[i]["datetime"]
                            in_ce_trade = False
                            stop_trading = False
                            previous_ce_sl_hit = True
                            is_gap_ce_sl = False
                            points_captured = entry - exit
                            exit_time = ce_df.iloc[i]["datetime"].time()
                            slippage = SLIPPAGE * (entry + exit)
                            pnl = qty * (points_captured - slippage)
                            # pnl=(qty*(points_captured-slippage))-qty*(otm_exit-otm_entry)
                            remark = "SL hit"
                            weekday_int = entry_date.weekday()
                            weekday_name = [
                                "Monday",
                                "Tuesday",
                                "Wednesday",
                                "Thursday",
                                "Friday",
                                "Saturday",
                                "Sunday",
                            ][weekday_int]
                            trade = {
                                "date": entry_date,
                                "day": weekday_name,
                                "expiry": expiry,
                                "DTE": (nearest_expiry - entry_date).days,
                                # 'atm' : atm,
                                # 'scrip' : index ,
                                "strike": strike,
                                "type": asset_class,
                                "Entry Price": entry,
                                "Entry Time": entry_time,
                                "initial sl": initial_sl,
                                # "TSL": tsl_high,
                                # 'OTM Entry' : otm_entry,
                                "Exit Price": exit,
                                "Exit date": ce_df.iloc[i]["datetime"].date(),
                                "Exit Time": exit_time,
                                'RSI on Entry': entry_rsi,
                                # 'OTM EXIT ' : otm_exit,
                                "Remark": remark,
                                "Points Captured": points_captured,
                                "Slippage": slippage,
                                # 'OTM cost' : otm_exit-otm_entry,
                                "Qty": qty,
                                "PnL": pnl,
                                "ROI%": (pnl / PORTFOLIO_VALUE) * 100,
                                "Trade Year": ce_df.iloc[i]["datetime"].year,
                                "Trade Month": ce_df.iloc[i]["datetime"].month,
                                "Highest High": ce_highest_high,  # Add highest high to trade data
                                "Lowest Low": ce_lowest_low,  # Add lowest low to trade data
                                "Max ROI%": (
                                    (qty * (entry - ce_lowest_low)) / PORTFOLIO_VALUE
                                )
                                * 100,
                                "Margin": (
                                    (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                                )
                                * 100,
                            }
                            # print(trade)
                            trade_book.append(trade)
                            # tsl_high = 0
                            points_captured = 0
                            current_date = ce_df.iloc[i]["datetime"].date()
                            current_date_increament_flag = True
                            time_of_day = ce_df.iloc[i]["datetime"].time()
                            # print(f'current date changed to : {current_date} and time to {time_of_day}')
                            break

                        if (
                            in_ce_trade
                            and ce_df.iloc[i]["datetime"].date() == nearest_expiry
                            and ce_df.iloc[i]['datetime'].time() >= dt.time(15, 20)
                        ):
                            # print(ce_df.iloc[i])
                            # print(f'EOD exit {current_candle_close}')
                            # print(f'EOD datetime {ce_df.iloc[i]["datetime"]}')
                            exit = current_candle_close
                            otm_datetime = ce_df.iloc[i]["datetime"]
                            in_ce_trade = False
                            previous_ce_sl_hit = True
                            is_gap_ce_sl = False
                            points_captured = entry - exit
                            exit_time = ce_df.iloc[i]["datetime"].time()
                            slippage = SLIPPAGE * (entry + exit)
                            pnl = qty * (points_captured - slippage)
                            # pnl=(qty*(points_captured-slippage))-qty*(otm_exit-otm_entry)
                            remark = "EOD exit"
                            weekday_int = entry_date.weekday()
                            weekday_name = [
                                "Monday",
                                "Tuesday",
                                "Wednesday",
                                "Thursday",
                                "Friday",
                                "Saturday",
                                "Sunday",
                            ][weekday_int]
                            trade = {
                                "date": entry_date,
                                "day": weekday_name,
                                "expiry": expiry,
                                "DTE": (nearest_expiry - entry_date).days,
                                # 'atm' : atm,
                                # 'scrip' : index ,
                                "strike": strike,
                                "type": asset_class,
                                "Entry Price": entry,
                                "Entry Time": entry_time,
                                "initial sl": initial_sl,
                                # "TSL": tsl_high,
                                # 'OTM Entry' : otm_entry,
                                "Exit Price": exit,
                                "Exit date": ce_df.iloc[i]["datetime"].date(),
                                "Exit Time": exit_time,
                                'RSI on Entry': entry_rsi,
                                # 'OTM EXIT ' : otm_exit,
                                "Remark": remark,
                                "Points Captured": points_captured,
                                "Slippage": slippage,
                                # 'OTM cost' : otm_exit-otm_entry,
                                "Qty": qty,
                                "PnL": pnl,
                                "ROI%": (pnl / PORTFOLIO_VALUE) * 100,
                                "Trade Year": ce_df.iloc[i]["datetime"].year,
                                "Trade Month": ce_df.iloc[i]["datetime"].month,
                                "Highest High": ce_highest_high,  # Add highest high to trade data
                                "Lowest Low": ce_lowest_low,  # Add lowest low to trade data
                                "Max ROI%": (
                                    (qty * (entry - ce_lowest_low)) / PORTFOLIO_VALUE
                                )
                                * 100,
                                "Margin": (
                                    (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                                )
                                * 100,
                            }
                            # print(trade)
                            trade_book.append(trade)
                            # tsl_high = 0
                            points_captured = 0
                            current_date = nearest_expiry + dt.timedelta(days=1)
                            current_date_increament_flag = True
                            time_of_day = dt.time(9, 15)
                            # print(f'current date increased by 1 on expiry : {current_date}')
                            break

                        if (
                            not in_ce_trade
                            and not previous_ce_sl_hit
                            and ce_df.iloc[i]["datetime"].time() > dt.time(15, 15)
                        ):
                            # print('inside exoiry non trade date increment')
                            current_date = current_date + dt.timedelta(days=1)
                            current_date_increament_flag = True
                            time_of_day = dt.time(9, 15)
                            break

        if not current_date_increament_flag:
            current_date = current_date + dt.timedelta(days=1)
            current_date_increament_flag = False

    trade_book_df = pd.DataFrame(trade_book)

    return trade_book_df

In [32]:
async def pe_trade(data, st_high, ema, pct, start_date, end_date):
    df = data.copy()

    # start_date = dt.date(2025, 5, 9)
    # end_date = dt.date(2025, 5, 31)
    
    current_date = start_date

    combined_trades = pd.DataFrame()
    total_trades = pd.DataFrame()
    time_of_day = dt.time(9, 15)
    trade_book = []
    pe_lowest_low = float("inf")
    pe_highest_high = float("-inf")
    entry_rsi = 0

    while current_date < end_date:
        print(f'PE : {current_date}')
        entry = 0
        initial_sl = 0
        exit = 0
        in_pe_trade = False
        in_pe_trade = False
        # signal_exist=False

        points_captured = 0
        remark = ""
        trailing_active = False
        tsl = 0
        stop_trading = False
        is_gap_pe_sl = False
        previous_pe_sl_hit = False
        current_date_increament_flag = False
        # tsl_high = 0

        starting_time = dt.time(9, 15)

        ending_time = dt.time(15, 30)

        if not in_pe_trade and current_date in trading_days_set:

            pe_search_datetime = dt.datetime.combine(current_date, time_of_day)
            # print(f'current date : {pe_search_datetime}')

            spot_open = df.loc[df["datetime"] >= pe_search_datetime, "o"].iloc[0]
            print(f'spot open : {spot_open}')
            # spot_atm = int(round(spot_open / INDEX_MROUND) * INDEX_MROUND)
            spot_atm = int(
                math.floor(spot_open / INDEX_MROUND) * INDEX_MROUND
            )  ##ROUNDS TO NEAREST 500 OTM
            # print(f'spot atm : {spot_atm}')
            # nearest_expiry = await get_expiry(current_date)
            nearest_expiry = await get_expiry_nifty(current_date)
            # if current_date== nearest_expiry:
            #     next_expiry_passing_value = current_date + dt.timedelta(days=1)
            #     nearest_expiry = await get_expiry_nifty( next_expiry_passing_value)
            # print(f'passing date for expry : {current_date}')
            # nearest_expiry = await get_monthly_expiry_nifty(current_date)
            # print(f'nearest expiry{nearest_expiry}')
            selected_strike_pe = spot_atm
            print(f'selected strike PE : {selected_strike_pe}')
            pe_df = await fetch_data(
                index=INDEX,
                start_date=nearest_expiry - dt.timedelta(days=7),
                start_time=starting_time,
                end_date=nearest_expiry,
                end_time=ending_time,
                strike=selected_strike_pe,
                asset_class="P",
                expiry=nearest_expiry,
            )
            if pe_df is not None and not isinstance(pe_df, str):
                # print('new data fetched PE')
                data_pe = True
                pe_df = pe_df.select(["datetime", "o", "h", "l", "c", "v"])
                pe_df = resample(pe_df, TF)
                pe_df_pandas = pe_df.to_pandas()
                pe_df = generate_signals(pe_df_pandas, st_high, ema, pct)
                # pe_df = calculate_signals(pe_df_pandas)
                print(pe_df.to_string())
            else:
                data_pe = False
                current_date += dt.timedelta(days=1)
                continue

            if data_pe:

                for i in range(0, len(pe_df)):
                    current_candle = pe_df.iloc[i]
                    current_candle_open = pe_df.iloc[i]["o"]
                    current_candle_high = pe_df.iloc[i]["h"]
                    current_candle_low = pe_df.iloc[i]["l"]
                    current_candle_close = pe_df.iloc[i]["c"]

                    previous_candle_low = pe_df.iloc[i - 1]["l"]
                    previous_candle_close = pe_df.iloc[i - 1]["c"]
                    

                    expiry = nearest_expiry
                    strike = selected_strike_pe
                    asset_class = "P"
                    # print(pe_df.iloc[i])

                    signal = pe_df.iloc[i - 1]["Sell Signal"]
                    # candle_condition = (pe_df.iloc[i-1]['daily_high_till_now'] - previous_candle_close) > 10

                    if pe_df.iloc[i]["datetime"] >= pe_search_datetime:


                        if (
                            not previous_pe_sl_hit
                            and not in_pe_trade
                            and signal
                            # and current_candle_low < previous_candle_low
                            and pe_df.iloc[i]["datetime"].time() > time_of_day
                            and (
                                (nearest_expiry - pe_df.iloc[i]["datetime"].date()).days
                                >= 0
                                and (
                                    nearest_expiry - pe_df.iloc[i]["datetime"].date()
                                ).days
                                < 8
                            )
                            and pe_df.iloc[i]["datetime"].time() < dt.time(15, 25)
                            # and candle_condition
                        ):
                            # print(pe_df.iloc[i-1])
                            # print(f'entry found {previous_candle_low}')
                            # print(f'entry datetime {pe_df.iloc[i]["datetime"]}')
                            
                            # today_data = pe_df[pe_df['datetime'].dt.date == current_candle['datetime'].date()]
                            # day_high = today_data.iloc[0 : i]['h'].max()
                            # print(today_data.to_string())
                            
                            entry = current_candle_open
                            entry_date = pe_df.iloc[i-1]["datetime"].date()
                            entry_time = pe_df.iloc[i-1]["datetime"].time()
                            # initial_sl = pe_df.iloc[i - SL_CANDLES_NUM : i]["h"].max()
                            # initial_sl = day_high
                            initial_sl = pe_df.iloc[i-1]['daily_high_till_now']
                            in_pe_trade = True
                            pe_lowest_low = float("inf")
                            pe_highest_high = float("-inf")
                            # entry_rsi = pe_df.iloc[i-1]['RSI']

                            qty = RPT_PE * PORTFOLIO_VALUE / (initial_sl - entry)
                            if (
                                (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                            ) * 100 > MAX_MARGIN:
                                qty = PORTFOLIO_VALUE * INDEX_LEV / strike * (MAX_MARGIN / 100)

                        # While in trade, track the highest high and lowest low
                        if in_pe_trade:
                            # Track the highest high
                            pe_highest_high = max(pe_highest_high, current_candle_high)

                            # Track the lowest low
                            pe_lowest_low = min(pe_lowest_low, current_candle_low)

                            # if all(
                            #     pe_df.loc[i - j, "h"] <= pe_df.loc[i - fractal_num, "h"]
                            #     for j in range(0, ((fractal_num * 2) + 1))
                            # ):
                            #     tsl_high = pe_df.loc[i - fractal_num, "h"]

                        if (
                            in_pe_trade
                            and pe_df.iloc[i]["datetime"].time() == dt.time(9, 15)
                            and current_candle_open > initial_sl
                        ):

                            # print(pe_df.iloc[i])
                            # print(f'GAP sl hit {initial_sl}')
                            # print(f'GAP sl datetime {pe_df.iloc[i]["datetime"]}')
                            exit = current_candle_close
                            in_pe_trade = False
                            stop_trading = False
                            previous_pe_sl_hit = True
                            is_gap_pe_sl = False
                            points_captured = entry - exit
                            exit_time = pe_df.iloc[i]["datetime"].time()
                            slippage = SLIPPAGE * (entry + exit)
                            pnl = qty * (points_captured - slippage)
                            remark = "Gap SL hit"
                            weekday_int = entry_date.weekday()
                            weekday_name = [
                                "Monday",
                                "Tuesday",
                                "Wednesday",
                                "Thursday",
                                "Friday",
                                "Saturday",
                                "Sunday",
                            ][weekday_int]
                            trade = {
                                "date": entry_date,
                                "day": weekday_name,
                                "expiry": expiry,
                                "DTE": (nearest_expiry - entry_date).days,
                                # 'atm' : atm,
                                # 'scrip' : index ,
                                "strike": strike,
                                "type": asset_class,
                                "Entry Price": entry,
                                "Entry Time": entry_time,
                                "initial sl": initial_sl,
                                # "TSL": tsl_high,
                                # 'OTM Entry' : otm_entry,
                                "Exit Price": exit,
                                "Exit date": pe_df.iloc[i]["datetime"].date(),
                                "Exit Time": exit_time,
                                'RSI on Entry': entry_rsi,
                                # 'OTM EXIT ' : otm_exit,
                                "Remark": remark,
                                "Points Captured": points_captured,
                                "Slippage": slippage,
                                # 'OTM cost' : otm_exit-otm_entry,
                                "Qty": qty,
                                "PnL": pnl,
                                "ROI%": (pnl / PORTFOLIO_VALUE) * 100,
                                "Trade Year": pe_df.iloc[i]["datetime"].year,
                                "Trade Month": pe_df.iloc[i]["datetime"].month,
                                "Highest High": pe_highest_high,  # Add highest high to trade data
                                "Lowest Low": pe_lowest_low,  # Add lowest low to trade data
                                "Max ROI%": (
                                    (qty * (entry - pe_lowest_low)) / PORTFOLIO_VALUE
                                )
                                * 100,
                                "Margin": (
                                    (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                                )
                                * 100,
                            }
                            # print(trade)
                            trade_book.append(trade)
                            # tsl_high = 0
                            points_captured = 0
                            current_date = pe_df.iloc[i]["datetime"].date()
                            current_date_increament_flag = True
                            time_of_day = pe_df.iloc[i]["datetime"].time()
                            # print(f'current date changed to : {current_date} and time to {time_of_day}')
                            break

                        if in_pe_trade and current_candle_high > initial_sl:
                            # print(pe_df.iloc[i])
                            # print(f'initial sl hit {initial_sl}')
                            # print(f'initial sl datetime {pe_df.iloc[i]["datetime"]}')
                            exit = initial_sl
                            otm_datetime = pe_df.iloc[i]["datetime"]
                            in_pe_trade = False
                            stop_trading = False
                            previous_pe_sl_hit = True
                            is_gap_pe_sl = False
                            points_captured = entry - exit
                            exit_time = pe_df.iloc[i]["datetime"].time()
                            slippage = SLIPPAGE * (entry + exit)
                            pnl = qty * (points_captured - slippage)
                            # pnl=(qty*(points_captured-slippage))-qty*(otm_exit-otm_entry)
                            remark = "SL hit"
                            weekday_int = entry_date.weekday()
                            weekday_name = [
                                "Monday",
                                "Tuesday",
                                "Wednesday",
                                "Thursday",
                                "Friday",
                                "Saturday",
                                "Sunday",
                            ][weekday_int]
                            trade = {
                                "date": entry_date,
                                "day": weekday_name,
                                "expiry": expiry,
                                "DTE": (nearest_expiry - entry_date).days,
                                # 'atm' : atm,
                                # 'scrip' : index ,
                                "strike": strike,
                                "type": asset_class,
                                "Entry Price": entry,
                                "Entry Time": entry_time,
                                "initial sl": initial_sl,
                                # "TSL": tsl_high,
                                # 'OTM Entry' : otm_entry,
                                "Exit Price": exit,
                                "Exit date": pe_df.iloc[i]["datetime"].date(),
                                "Exit Time": exit_time,
                                'RSI on Entry': entry_rsi,
                                # 'OTM EXIT ' : otm_exit,
                                "Remark": remark,
                                "Points Captured": points_captured,
                                "Slippage": slippage,
                                # 'OTM cost' : otm_exit-otm_entry,
                                "Qty": qty,
                                "PnL": pnl,
                                "ROI%": (pnl / PORTFOLIO_VALUE) * 100,
                                "Trade Year": pe_df.iloc[i]["datetime"].year,
                                "Trade Month": pe_df.iloc[i]["datetime"].month,
                                "Highest High": pe_highest_high,  # Add highest high to trade data
                                "Lowest Low": pe_lowest_low,  # Add lowest low to trade data
                                "Max ROI%": (
                                    (qty * (entry - pe_lowest_low)) / PORTFOLIO_VALUE
                                )
                                * 100,
                                "Margin": (
                                    (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                                )
                                * 100,
                            }
                            # print(trade)
                            trade_book.append(trade)
                            tsl_high = 0
                            points_captured = 0
                            current_date = pe_df.iloc[i]["datetime"].date()
                            current_date_increament_flag = True
                            time_of_day = pe_df.iloc[i]["datetime"].time()
                            # print(f'current date changed to : {current_date} and time to {time_of_day}')
                            break

                        if (
                            in_pe_trade
                            and pe_df.iloc[i]["datetime"].date() == nearest_expiry
                            and pe_df.iloc[i]['datetime'].time() >= dt.time(15, 20)
                        ):
                            # print(pe_df.iloc[i])
                            # print(f'EOD exit {current_candle_close}')
                            # print(f'EOD datetime {pe_df.iloc[i]["datetime"]}')
                            exit = current_candle_close
                            otm_datetime = pe_df.iloc[i]["datetime"]
                            in_pe_trade = False
                            previous_pe_sl_hit = True
                            is_gap_pe_sl = False
                            points_captured = entry - exit
                            exit_time = pe_df.iloc[i]["datetime"].time()
                            slippage = SLIPPAGE * (entry + exit)
                            pnl = qty * (points_captured - slippage)
                            # pnl=(qty*(points_captured-slippage))-qty*(otm_exit-otm_entry)
                            remark = "EOD exit"
                            weekday_int = entry_date.weekday()
                            weekday_name = [
                                "Monday",
                                "Tuesday",
                                "Wednesday",
                                "Thursday",
                                "Friday",
                                "Saturday",
                                "Sunday",
                            ][weekday_int]
                            trade = {
                                "date": entry_date,
                                "day": weekday_name,
                                "expiry": expiry,
                                "DTE": (nearest_expiry - entry_date).days,
                                # 'atm' : atm,
                                # 'scrip' : index ,
                                "strike": strike,
                                "type": asset_class,
                                "Entry Price": entry,
                                "Entry Time": entry_time,
                                "initial sl": initial_sl,
                                # "TSL": tsl_high,
                                # 'OTM Entry' : otm_entry,
                                "Exit Price": exit,
                                "Exit date": pe_df.iloc[i]["datetime"].date(),
                                "Exit Time": exit_time,
                                'RSI on Entry': entry_rsi,
                                # 'OTM EXIT ' : otm_exit,
                                "Remark": remark,
                                "Points Captured": points_captured,
                                "Slippage": slippage,
                                # 'OTM cost' : otm_exit-otm_entry,
                                "Qty": qty,
                                "PnL": pnl,
                                "ROI%": (pnl / PORTFOLIO_VALUE) * 100,
                                "Trade Year": pe_df.iloc[i]["datetime"].year,
                                "Trade Month": pe_df.iloc[i]["datetime"].month,
                                "Highest High": pe_highest_high,  # Add highest high to trade data
                                "Lowest Low": pe_lowest_low,  # Add lowest low to trade data
                                "Max ROI%": (
                                    (qty * (entry - pe_lowest_low)) / PORTFOLIO_VALUE
                                )
                                * 100,
                                "Margin": (
                                    (qty * strike) / (INDEX_LEV * PORTFOLIO_VALUE)
                                )
                                * 100,
                            }
                            # print(trade)
                            trade_book.append(trade)
                            # tsl_high = 0
                            points_captured = 0
                            current_date = nearest_expiry + dt.timedelta(days=1)
                            current_date_increament_flag = True
                            time_of_day = dt.time(9, 15)
                            # print(f'current date increased by 1 on expiry : {current_date}')
                            break

                        if (
                            not in_pe_trade
                            and not previous_pe_sl_hit
                            and pe_df.iloc[i]["datetime"].time() > dt.time(15, 15)
                        ):
                            # print('inside exoiry non trade date increment')
                            current_date = current_date + dt.timedelta(days=1)
                            current_date_increament_flag = True
                            time_of_day = dt.time(9, 15)
                            break

        if not current_date_increament_flag:
            current_date = current_date + dt.timedelta(days=1)
            current_date_increament_flag = False

    trade_book_df = pd.DataFrame(trade_book)

    return trade_book_df

In [33]:
async def execute(DF, n, rsi_n, rsi_overbought, start_date, end_date):
    data = DF.copy()
    tb_ce = await ce_trade(data, n, rsi_n, rsi_overbought, start_date, end_date)
    tb_pe = await pe_trade(data, n, rsi_n, rsi_overbought, start_date, end_date)
    tb = pd.concat([tb_ce, tb_pe], ignore_index=True)
    # print(len(tb))
    if len(tb)>0:
        tb = tb.sort_values(by="date")
    return tb

In [34]:
def generate_stats(tb_expiry, ema_window):
    stats_df8 = pd.DataFrame(
        index=range(2019, 2026),
        columns=[
            "Total ROI",
            "Total Trades",
            "Win Rate",
            "Avg Profit% per Trade",
            "Avg Loss% per Trade",
            "Max Drawdown",
            "ROI/DD Ratio",
            "Variation",
        ],
    )
    combined_df_sorted = tb_expiry
    # combined_df_sorted = tb_expiry_ce
    # combined_df_sorted = tb_expiry_pe

    # Iterate over each year
    for year in range(2019, 2026):
        # Filter trades for the current year
        year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

        # Calculate total ROI
        total_roi = year_trades["ROI%"].sum()

        # Calculate total number of trades
        total_trades = len(year_trades)

        # Calculate win rate
        win_rate = (year_trades["ROI%"] > 0).mean() * 100

        # Calculate average profit per trade
        avg_profit = year_trades[year_trades["ROI%"] > 0]["ROI%"].mean()

        # Calculate average loss per trade
        avg_loss = year_trades[year_trades["ROI%"] < 0]["ROI%"].mean()

        # Calculate maximum drawdown
        max_drawdown = (
            year_trades["ROI%"].cumsum() - year_trades["ROI%"].cumsum().cummax()
        ).min()

        # Calculate ROI/DD ratio
        roi_dd_ratio = total_roi / abs(max_drawdown)

        variation = f"{ema_window}"

        # Store the statistics in the DataFrame
        stats_df8.loc[year] = [
            total_roi,
            total_trades,
            win_rate,
            avg_profit,
            avg_loss,
            max_drawdown,
            roi_dd_ratio,
            variation,
        ]

    # Calculate overall statistics
    overall_total_roi = stats_df8["Total ROI"].sum()
    overall_total_trades = stats_df8["Total Trades"].sum()
    overall_win_rate = (combined_df_sorted["ROI%"] > 0).mean() * 100
    overall_avg_profit = combined_df_sorted[combined_df_sorted["ROI%"] > 0][
        "ROI%"
    ].mean()
    overall_avg_loss = combined_df_sorted[combined_df_sorted["ROI%"] < 0]["ROI%"].mean()
    overall_max_drawdown = (
        combined_df_sorted["ROI%"].cumsum()
        - combined_df_sorted["ROI%"].cumsum().cummax()
    ).min()
    overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)
    overall_variation = variation

    # Store the overall statistics in the DataFrame
    stats_df8.loc["Overall"] = [
        overall_total_roi,
        overall_total_trades,
        overall_win_rate,
        overall_avg_profit,
        overall_avg_loss,
        overall_max_drawdown,
        overall_roi_dd_ratio,
        overall_variation,
    ]
    return {overall_roi_dd_ratio: stats_df8}

In [37]:
# short_ma = 4
# long_ma = 12
# signal_window = 9
# ema_window = 25
# n = 4
# rsi_n = 6
# rsi_overbought = 45

start_date = dt.date(2025, 3, 28)
end_date = dt.date(2025, 5, 31)

tb = await execute(data, 49, 50000, 0.55, start_date, end_date)

CE : 2025-03-28
spot open : 23600.4
selected strike CE : 23650
shape: (1_879, 11)
┌───────┬─────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┐
│ index ┆ expiry  ┆ strike ┆ asset_ ┆ dateti ┆ o      ┆ h      ┆ l      ┆ c      ┆ v      ┆ oi     │
│ ---   ┆ ---     ┆ ---    ┆ class  ┆ me     ┆ ---    ┆ ---    ┆ ---    ┆ ---    ┆ ---    ┆ ---    │
│ str   ┆ datetim ┆ i64    ┆ ---    ┆ ---    ┆ f64    ┆ f64    ┆ f64    ┆ f64    ┆ i64    ┆ i64    │
│       ┆ e[μs]   ┆        ┆ str    ┆ dateti ┆        ┆        ┆        ┆        ┆        ┆        │
│       ┆         ┆        ┆        ┆ me[μs] ┆        ┆        ┆        ┆        ┆        ┆        │
╞═══════╪═════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╡
│ nifty ┆ 2025-04 ┆ 23650  ┆ C      ┆ 2025-0 ┆ 127.0  ┆ 127.0  ┆ 106.7  ┆ 109.9  ┆ 66826  ┆ 518850 │
│       ┆ -03 00: ┆        ┆        ┆ 3-27   ┆        ┆        ┆        ┆        ┆        ┆        │
│       ┆

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



CE : 2025-05-14
spot open : 24613.8
selected strike CE : 24650
shape: (2_255, 11)
┌───────┬─────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┐
│ index ┆ expiry  ┆ strike ┆ asset_ ┆ dateti ┆ o      ┆ h      ┆ l      ┆ c      ┆ v      ┆ oi     │
│ ---   ┆ ---     ┆ ---    ┆ class  ┆ me     ┆ ---    ┆ ---    ┆ ---    ┆ ---    ┆ ---    ┆ ---    │
│ str   ┆ datetim ┆ i64    ┆ ---    ┆ ---    ┆ f64    ┆ f64    ┆ f64    ┆ f64    ┆ i64    ┆ i64    │
│       ┆ e[μs]   ┆        ┆ str    ┆ dateti ┆        ┆        ┆        ┆        ┆        ┆        │
│       ┆         ┆        ┆        ┆ me[μs] ┆        ┆        ┆        ┆        ┆        ┆        │
╞═══════╪═════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╡
│ nifty ┆ 2025-05 ┆ 24650  ┆ C      ┆ 2025-0 ┆ 109.95 ┆ 122.85 ┆ 109.95 ┆ 114.3  ┆ 57904  ┆ 304275 │
│       ┆ -15 00: ┆        ┆        ┆ 5-08   ┆        ┆        ┆        ┆        ┆        ┆        │
│       ┆

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



PE : 2025-03-28
spot open : 23600.4
selected strike PE : 23600
               datetime        o        h        l        c         v  short_term_low  daily_high_till_now  Sell Signal
0   2025-03-27 09:15:00 204.0000 218.9000 179.5000 190.7500    878027             NaN             218.9000            0
1   2025-03-27 09:25:00 191.5500 198.0500 156.8000 175.5500    970125             NaN             218.9000            0
2   2025-03-27 09:35:00 175.6000 184.0000 155.4000 155.4000    631050             NaN             218.9000            0
3   2025-03-27 09:45:00 156.5000 171.4500 146.6500 149.5000    606375             NaN             218.9000            0
4   2025-03-27 09:55:00 149.5500 153.7000 135.4000 136.0000    729675             NaN             218.9000            0
5   2025-03-27 10:05:00 135.3500 140.9500 128.4000 137.1500    902550             NaN             218.9000            0
6   2025-03-27 10:15:00 136.6500 143.9000 129.2000 133.8000    902550             NaN            

In [21]:
tb['DATETIME'] = pd.to_datetime(tb['date'].astype(str) + ' ' + tb['Entry Time'].astype(str))

In [134]:
tb = tb.sort_values(by='DATETIME')
stats = generate_stats(tb, '...')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2019      81.3374           86  58.1395                3.6377   
2020     120.1328          109  57.7982                4.1602   
2021      88.7812          102  52.9412                4.4061   
2022      81.4753          105  54.2857                4.0705   
2023      56.6479          100  52.0000                3.6718   
2024     110.0350           97  58.7629                3.9316   
2025      44.9667           36  66.6667                3.6202   
Overall  583.3763          635  56.2205                3.9659   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation  
2019                -2.7929     -12.1393       6.7004       ...  
2020                -3.0861     -12.5725       9.5552       ...  
2021                -3.1072     -19.6211       4.5248       ...  
2022                -3.1363     -14.5782       5.5888       ...  
2023                -2.7977     -19.0605       2.9720       ...  
2024                -2.8517     -12.0344       9.1433       ...  
2025                -3.4931     -13.8576       3.2449       ...  
Overall             -2.9945     -20.4286      28.5568       ...

In [132]:
tb = tb.sort_values(by='DATETIME')
stats = generate_stats(tb, '...')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2019      81.3374           86  58.1395                3.6377   
2020     120.1328          109  57.7982                4.1602   
2021      88.7812          102  52.9412                4.4061   
2022      81.4753          105  54.2857                4.0705   
2023      56.6479          100  52.0000                3.6718   
2024     110.0350           97  58.7629                3.9316   
2025      44.9667           36  66.6667                3.6202   
Overall  583.3763          635  56.2205                3.9659   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation  
2019                -2.7929     -12.1393       6.7004       ...  
2020                -3.0861     -12.5725       9.5552       ...  
2021                -3.1072     -19.6211       4.5248       ...  
2022                -3.1363     -14.5782       5.5888       ...  
2023                -2.7977     -19.0605       2.9720       ...  
2024                -2.8517     -12.0344       9.1433       ...  
2025                -3.4931     -13.8576       3.2449       ...  
Overall             -2.9945     -20.4286      28.5568       ...

In [22]:
tb = tb.sort_values(by='DATETIME')
stats = generate_stats(tb, '...')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2019       0.0000            0      NaN                   NaN   
2020       0.0000            0      NaN                   NaN   
2021       0.0000            0      NaN                   NaN   
2022       0.0000            0      NaN                   NaN   
2023       0.0000            0      NaN                   NaN   
2024       0.0000            0      NaN                   NaN   
2025       9.6847           21  52.3810                4.1259   
Overall    9.6847           21  52.3810                4.1259   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation  
2019                    NaN          NaN          NaN       ...  
2020                    NaN          NaN          NaN       ...  
2021                    NaN          NaN          NaN       ...  
2022                    NaN          NaN          NaN       ...  
2023                    NaN          NaN          NaN       ...  
2024                    NaN          NaN          NaN       ...  
2025                -3.5700     -13.8576       0.6989       ...  
Overall             -3.5700     -13.8576       0.6989       ...

In [30]:
tb.tail(25)

date        day      expiry  DTE  strike type  Entry Price  \
0   2025-03-03     Monday  2025-03-06    3   22200    C     120.6500   
11  2025-03-05  Wednesday  2025-03-06    1   22050    P      32.3500   
1   2025-03-10     Monday  2025-03-13    3   22550    C     111.8500   
12  2025-03-10     Monday  2025-03-13    3   22500    P      69.2500   
13  2025-03-13   Thursday  2025-03-13    0   22500    P      38.4000   
14  2025-03-18    Tuesday  2025-03-20    2   22650    P      89.0000   
15  2025-03-24     Monday  2025-03-27    3   23500    P      98.9000   
2   2025-03-26  Wednesday  2025-03-27    1   23750    C      58.8000   
3   2025-03-28     Friday  2025-04-03    6   23650    C      90.9500   
16  2025-04-16  Wednesday  2025-04-17    1   23300    P      59.9000   
4   2025-04-17   Thursday  2025-04-17    0   23450    C      12.0500   
17  2025-04-22    Tuesday  2025-04-24    2   24150    P      85.2000   
5   2025-05-06    Tuesday  2025-05-08    2   24550    C      42.0500   
6   2025-05-09     Friday  2025-05-15    6   23950    C     242.3000   
18  2025-05-14  Wednesday  2025-05-15    1   24600    P      64.7500   
7   2025-05-14  Wednesday  2025-05-15    1   24650    C      78.5500   
8   2025-05-19     Monday  2025-05-22    3   25050    C     126.5000   
19  2025-05-26     Monday  2025-05-29    3   24900    P     143.4500   
9   2025-05-27    Tuesday  2025-05-29    2   25000    C     135.6000   
10  2025-05-28  Wednesday  2025-05-29    1   24850    C     149.2500   
20  2025-05-28  Wednesday  2025-05-29    1   24800    P     107.7000   

   Entry Time  initial sl  Exit Price   Exit date Exit Time  RSI on Entry  \
0    09:35:00    173.4000    173.4000  2025-03-05  11:35:00             0   
11   09:15:00     88.7500      0.0500  2025-03-06  15:25:00             0   
1    13:45:00    199.0000      0.0500  2025-03-13  15:25:00             0   
12   09:35:00    127.0000    127.0000  2025-03-10  14:15:00             0   
13   09:35:00     80.0000     80.0000  2025-03-13  11:35:00             0   
14   09:25:00    129.0500      0.0500  2025-03-20  15:25:00             0   
15   09:55:00    164.0000      0.1000  2025-03-27  15:25:00             0   
2    09:35:00    105.0000      0.1500  2025-03-27  15:25:00             0   
3    12:15:00    190.0000      0.0500  2025-04-03  15:25:00             0   
16   09:25:00    101.4000    101.4000  2025-04-16  10:25:00             0   
4    09:15:00     48.9500     48.9500  2025-04-17  09:45:00             0   
17   10:05:00    162.0000      0.1500  2025-04-24  15:25:00             0   
5    09:15:00     73.5500      0.0500  2025-05-08  15:25:00             0   
6    13:15:00    403.7000    647.7500  2025-05-12  09:15:00             0   
18   09:35:00    152.2000    152.2000  2025-05-14  12:45:00             0   
7    12:35:00    170.0000    170.0000  2025-05-15  10:35:00             0   
8    13:25:00    180.9500      0.0500  2025-05-22  15:25:00             0   
19   09:15:00    200.0000    200.0000  2025-05-26  10:35:00             0   
9    09:15:00    209.9500    209.9500  2025-05-27  11:25:00             0   
10   09:25:00    226.7000      0.0500  2025-05-29  15:25:00             0   
20   12:55:00    215.0000      0.0500  2025-05-29  15:25:00             0   

        Remark  Points Captured  Slippage       Qty          PnL    ROI%  \
0       SL hit         -52.7500    2.9405 5687.2038 -316723.2227 -3.1672   
11    EOD exit          32.3000    0.3240 5319.1489  170085.1064  1.7009   
1     EOD exit         111.8000    1.1190 3442.3408  381001.7212  3.8100   
12      SL hit         -57.7500    1.9625 5194.8052 -310194.8052 -3.1019   
13      SL hit         -41.6000    1.1840 7211.5385 -308538.4615 -3.0854   
14    EOD exit          88.9500    0.8905 7490.6367  659621.7228  6.5962   
15    EOD exit          98.8000    0.9900 4608.2949  450737.3272  4.5074   
2     EOD exit          58.6500    0.5895 6493.5065  377016.2338  3.7702   
3     EOD exit          90.9000    0.9100 3028

In [25]:
tb = tb.sort_values(by='DATETIME')
stats = generate_stats(tb, '...')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2019      81.3374           86  58.1395                3.6377   
2020     120.1328          109  57.7982                4.1602   
2021      88.7812          102  52.9412                4.4061   
2022      81.4753          105  54.2857                4.0705   
2023      56.6479          100  52.0000                3.6718   
2024     110.0350           97  58.7629                3.9316   
2025      46.1605           27  74.0741                3.3949   
Overall  584.5700          626  56.3898                3.9571   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation  
2019                -2.7929     -12.1393       6.7004       ...  
2020                -3.0861     -12.5725       9.5552       ...  
2021                -3.1072     -19.6211       4.5248       ...  
2022                -3.1363     -14.5782       5.5888       ...  
2023                -2.7977     -19.0605       2.9720       ...  
2024                -2.8517     -12.0344       9.1433       ...  
2025                -3.1055      -4.5683      10.1045       ...  
Overall             -2.9754     -20.4286      28.6152       ...

In [135]:
tb_margin = tb[tb['Margin'] > 100]
tb_margin['ROI%'].sum()

432.94532663721407

In [28]:
stats = generate_stats(tb, '...')
for x, y in stats.items():
    z = pd.DataFrame(y)
    break

z

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2019      81.3374           86  58.1395                3.6377   
2020     120.1328          109  57.7982                4.1602   
2021      88.7812          102  52.9412                4.4061   
2022      81.4753          105  54.2857                4.0705   
2023      56.6479          100  52.0000                3.6718   
2024     110.0350           97  58.7629                3.9316   
2025      46.1605           27  74.0741                3.3949   
Overall  584.5700          626  56.3898                3.9571   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation  
2019                -2.7929     -12.1393       6.7004       ...  
2020                -3.0861     -12.5725       9.5552       ...  
2021                -3.1072     -19.6211       4.5248       ...  
2022                -3.1363     -14.5782       5.5888       ...  
2023                -2.7977     -19.0605       2.9720       ...  
2024                -2.8517     -12.0344       9.1433       ...  
2025                -3.1055      -4.5683      10.1045       ...  
Overall             -2.9754     -20.4286      28.6152       ...

# Variation : Close below 49 candles LOW, Current High > 0.55 * Day High

# 10min BT Running for candle close below prev n candles low variation

In [136]:
tb['Cumulative ROI%'] = tb['ROI%'].cumsum()
tb['Max Cumulative ROI%'] = tb['Cumulative ROI%'].cummax()  # Maximum value so far
tb['DD'] = tb['Cumulative ROI%'] - tb['Max Cumulative ROI%']  # Drawdown
tb

date        day      expiry  DTE  strike type  Entry Price  \
0    2019-01-25     Friday  2019-01-31    6   10900    C      49.8500   
309  2019-02-12    Tuesday  2019-02-14    2   10850    P      24.1500   
1    2019-02-12    Tuesday  2019-02-14    2   10900    C      34.0000   
2    2019-02-18     Monday  2019-02-21    3   10750    C      41.0500   
310  2019-02-25     Monday  2019-02-28    3   10800    P      46.4000   
311  2019-02-25     Monday  2019-02-28    3   10800    P      42.3500   
3    2019-02-26    Tuesday  2019-02-28    2   10800    C      58.7000   
312  2019-03-01     Friday  2019-03-07    6   10800    P      48.3000   
4    2019-03-05    Tuesday  2019-03-07    2   10900    C      33.9000   
313  2019-03-11     Monday  2019-03-14    3   11050    P      37.1500   
314  2019-03-15     Friday  2019-03-20    5   11350    P      45.9000   
5    2019-03-20  Wednesday  2019-03-20    0   11600    C       2.8000   
6    2019-03-25     Monday  2019-03-28    3   11400    C      47.8500   
315  2019-03-26    Tuesday  2019-03-28    2   11350    P      16.5500   
316  2019-04-01     Monday  2019-04-04    3   11650    P      53.3000   
7    2019-04-02    Tuesday  2019-04-04    2   11750    C      27.3000   
8    2019-04-03  Wednesday  2019-04-04    1   11750    C      20.6000   
317  2019-04-05     Friday  2019-04-11    6   11600    P      33.8500   
318  2019-04-09    Tuesday  2019-04-11    2   11600    P      31.5500   
319  2019-04-12     Friday  2019-04-18    6   11600    P      43.1000   
9    2019-04-23    Tuesday  2019-04-25    2   11650    C      32.1500   
320  2019-04-24  Wednesday  2019-04-25    1   11600    P      15.7000   
10   2019-04-30    Tuesday  2019-05-02    2   11750    C      17.9500   
321  2019-04-30    Tuesday  2019-05-02    2   11700    P      18.4000   
11   2019-05-06     Monday  2019-05-09    3   11650    C      42.1000   
12   2019-05-13     Monday  2019-05-16    3   11300    C      73.2500   
322  2019-05-17     Friday  2019-05-23    6   11250    P     186.2000   
13   2019-05-23   Thursday  2019-05-23    0   11950    C      91.3500   
323  2019-05-27     Monday  2019-05-30    3   11850    P      49.6000   
14   2019-05-28    Tuesday  2019-05-30    2   12000    C      26.0000   
15   2019-05-31     Friday  2019-06-06    6   12000    C      42.6000   
324  2019-06-04    Tuesday  2019-06-06    2   12050    P      35.5000   
325  2019-06-11    Tuesday  2019-06-13    2   11950    P      46.3000   
16   2019-06-12  Wednesday  2019-06-13    1   12000    C      11.2000   
17   2019-06-14     Friday  2019-06-20    6   11950    C      19.1000   
18   2019-06-21     Friday  2019-06-27    6   11850    C      31.4500   
326  2019-06-25    Tuesday  2019-06-27    2   11650    P      22.6000   
19   2019-06-28     Friday  2019-07-04    6   11900    C      43.3000   
327  2019-07-01     Monday  2019-07-04    3   11800    P      29.3000   
20   2019-07-05     Friday  2019-07-11    6   12000    C      56.2500   
328  2019-07-11   Thursday  2019-07-11    0   11550    P      16.8000   
329  2019-07-12     Friday  2019-07-18    6   11600    P      62.8500   
330  2019-07-16    Tuesday  2019-07-18    2   11550    P      22.7500   
21   2019-07-22     Monday  2019-07-25    3   11400    C      32.0500   
331  2019-07-23    Tuesday  2019-07-25    2   11350    P      39.7500   
22   2019-07-31  Wednesday  2019-08-01    1   11050    C      33.6000   
23   2019-08-01   Thursday  2019-08-01    0   11100    C       6.8500   
24   2019-08-05     Monday  2019-08-08    3   10900    C      63.8500   
25   2019-08-07  Wednesday  2019-08-08    1   11000    C      20.6000   
332  2019-08-09     Friday  2019-08-14    5   11050    P      52.8000   
26   2019-08-20    Tuesday  2019-08-22    2   11100    C      34.7500   
333  2019-08-27    Tuesday  2019-08-29    2   11100    P      54.5000   
27   2019-08-28  Wednesday  2019-08-29    1   11150    C      21.3500   
28   2019-08-30     Friday  2019-09-05    6   11000    C      55.1500

In [37]:
tb.to_csv('NLC_4x300.csv')

In [24]:
#10min
stats_dictionary = {}
for i in range(12, 49, 4):
    for j in range(20, 71, 10):
        print(f'{i}, {j/100}%')
        tb = await execute(data, i, 5, j/100)
        if len(tb) > 0:
            stats = generate_stats(tb, f'{i}, {j/100}%')
            for x, y in stats.items():
                z = pd.DataFrame(y)
                print(z.to_string())
                stats_dictionary[x] = y

12, 0.2%


/tmp/ipykernel_59697/1336650796.py:146: RuntimeWarning: divide by zero encountered in scalar divide
  qty = RPT_CE * PORTFOLIO_VALUE / (initial_sl - entry)


        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation
2019     173.4280          172  51.1628                4.7549             -2.9168     -19.2316       9.0179  12, 0.2%
2020     188.7499          210  45.2381                5.5258             -2.9235     -15.2785      12.3540  12, 0.2%
2021     101.4692          199  45.2261                4.6568             -2.9142     -30.0203       3.3800  12, 0.2%
2022      46.0617          218  42.2018                5.2306             -3.4536     -51.5416       0.8937  12, 0.2%
2023      47.6809          199  44.2211                4.0742             -2.8004     -26.7550       1.7821  12, 0.2%
2024      41.7527          150  40.6667                4.7623             -2.7949     -39.1397       1.0668  12, 0.2%
Overall  599.1424         1148  44.7735                4.8497             -2.9867     -51.5416      11.6244  12, 0.2%
12, 0.3%


/tmp/ipykernel_59697/1336650796.py:146: RuntimeWarning: divide by zero encountered in scalar divide
  qty = RPT_CE * PORTFOLIO_VALUE / (initial_sl - entry)


        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation
2019     172.8051          170  50.5882                4.8583             -2.9168     -22.4432       7.6997  12, 0.3%
2020     187.6521          209  44.9761                5.5729             -2.9235     -15.2785      12.2821  12, 0.3%
2021     100.9231          198  44.9495                4.7030             -2.9142     -30.0203       3.3618  12, 0.3%
2022      46.0617          218  42.2018                5.2306             -3.4536     -55.3935       0.8315  12, 0.3%
2023      45.8014          195  43.0769                4.2458             -2.8004     -32.6027       1.4048  12, 0.3%
2024      40.5747          148  39.8649                4.9037             -2.7949     -37.8598       1.0717  12, 0.3%
Overall  593.8180         1138  44.2882                4.9353             -2.9867     -55.3935      10.7200  12, 0.3%
12, 0.4%


...

        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation
2019     137.4240          141  56.0284                3.9063             -2.7608     -15.8885       8.6493  24, 0.4%
2020     199.4769          172  50.5814                5.0862             -2.8590     -13.6529      14.6106  24, 0.4%
2021      78.3394          169  49.7041                4.0433             -3.0741     -31.1025       2.5187  24, 0.4%
2022      32.6532          178  43.2584                4.6343             -3.2098     -37.0854       0.8805  24, 0.4%
2023      59.5495          163  46.0123                3.9260             -2.6693     -26.8461       2.2182  24, 0.4%
2024      60.4861          118  42.3729                4.8303             -2.6622     -21.7193       2.7849  24, 0.4%
Overall  567.9291          941  48.0340                4.3884             -2.8949     -37.0854      15.3141  24, 0.4%
24, 0.5%


/tmp/ipykernel_59697/1336650796.py:146: RuntimeWarning: divide by zero encountered in scalar divide
  qty = RPT_CE * PORTFOLIO_VALUE / (initial_sl - entry)


        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation
2019     136.2880          128  55.4688                4.2017             -2.8427     -18.5782       7.3359  24, 0.5%
2020     183.2379          159  50.9434                5.0954             -2.9421     -12.5276      14.6267  24, 0.5%
2021      81.1690          155  47.7419                4.5487             -3.1536     -29.3922       2.7616  24, 0.5%
2022      43.8370          170  44.1176                4.6993             -3.2485     -32.5623       1.3463  24, 0.5%
2023      46.6809          157  45.2229                3.9892             -2.7506     -29.1675       1.6004  24, 0.5%
2024      69.7482          110  43.6364                5.0277             -2.7674     -13.8796       5.0252  24, 0.5%
Overall  560.9610          879  47.7816                4.5825             -2.9710     -32.5623      17.2273  24, 0.5%
24, 0.6%


/tmp/ipykernel_59697/1336650796.py:146: RuntimeWarning: divide by zero encountered in scalar divide
  qty = RPT_CE * PORTFOLIO_VALUE / (initial_sl - entry)


        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation
2019     109.9116          115  50.4348                4.6642             -2.8178     -24.4122       4.5023  24, 0.6%
2020     155.0865          147  51.7007                4.8933             -3.0536     -12.5276      12.3796  24, 0.6%
2021      59.0946          141  44.6809                4.9351             -3.2284     -33.6146       1.7580  24, 0.6%
2022      47.6104          151  43.7086                4.9703             -3.2992     -24.2691       1.9618  24, 0.6%
2023      34.9851          138  44.2029                4.1897             -2.8648     -30.5597       1.1448  24, 0.6%
2024      61.5091           97  42.2680                5.4380             -2.8830     -14.9063       4.1264  24, 0.6%
Overall  468.1974          789  46.2611                4.8216             -3.0465     -33.6146      13.9284  24, 0.6%
24, 0.7%
        Total ROI Total Trades Win Rate Avg Pro

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt

def plot_sum_roi_by_dte(tb):
    """
    Plots the sum of ROI% across all unique DTE values.

    Parameters:
    tb (pd.DataFrame): Input DataFrame with 'DTE' and 'ROI%' columns.
    """
    # Ensure the DataFrame contains the required columns
    required_columns = {'DTE', 'ROI%'}
    if not required_columns.issubset(tb.columns):
        raise ValueError(f"Input DataFrame must contain columns: {required_columns}")
    
    # Group by DTE and calculate the sum of ROI%
    result = tb.groupby('DTE', as_index=False)['ROI%'].sum()
    result.rename(columns={'ROI%': 'Sum_ROI%'}, inplace=True)

    # Plot the data
    plt.figure(figsize=(10, 6))
    plt.bar(result['DTE'], result['Sum_ROI%'], color='skyblue', edgecolor='black')
    
    # Add labels and title
    plt.title('Sum of ROI% Across Unique DTE Values', fontsize=14)
    plt.xlabel('DTE', fontsize=12)
    plt.ylabel('Sum of ROI%', fontsize=12)
    plt.xticks(rotation=45, fontsize=10)
    plt.grid(axis='y', linestyle='--', alpha=0.7)
    
    # Show the plot
    plt.tight_layout()
    plt.show()

# Example usage
# tb = pd.DataFrame({'DTE': [...], 'ROI%': [...]})  # Replace with your actual DataFrame
plot_sum_roi_by_dte(tb)


In [92]:
def calculate_max_dd(tb):
    """
    Calculates the maximum drawdown for each group of 'DTE'.
    
    Parameters:
    tb (pd.DataFrame): Input DataFrame with 'DTE' and 'ROI%' columns.
    
    Returns:
    pd.Series: Maximum drawdown for each unique DTE.
    """
    # Calculate cumulative sum of ROI%
    cumulative_returns = tb["ROI%"].cumsum()
    
    # Calculate maximum drawdown
    max_drawdown = (cumulative_returns - cumulative_returns.cummax()).min()
    
    return max_drawdown


In [ ]:
def plot_sum_roi_and_max_dd_by_dte(tb):
    """
    Plots the sum of ROI% and Absolute Max Drawdown (Max DD) across all unique DTE values
    using a single Y-axis, and prints the resulting DataFrame.

    Parameters:
    tb (pd.DataFrame): Input DataFrame with 'DTE' and 'ROI%' columns.
    """
    # Ensure the DataFrame contains the required columns
    required_columns = {'DTE', 'ROI%'}
    if not required_columns.issubset(tb.columns):
        raise ValueError(f"Input DataFrame must contain columns: {required_columns}")
    
    # Group by DTE and calculate the sum of ROI%
    roi_result = tb.groupby('DTE', as_index=False)['ROI%'].sum()
    roi_result.rename(columns={'ROI%': 'Sum_ROI%'}, inplace=True)

    # Group by DTE and calculate Max DD (in absolute terms)
    dd_result = tb.groupby('DTE').apply(calculate_max_dd).reset_index()
    dd_result.rename(columns={0: 'Max_DD%'}, inplace=True)
    dd_result['Max_DD%'] = dd_result['Max_DD%'].abs()

    # Merge the sum of ROI% and Max DD data
    result = pd.merge(roi_result, dd_result, on='DTE')

    # Add ROI% / Max DD ratio
    result['ROI/DD_Ratio'] = result.apply(
        lambda row: row['Sum_ROI%'] / row['Max_DD%'] if row['Max_DD%'] != 0 else float('inf'), axis=1
    )

    # Format values
    result['Sum_ROI%'] = result['Sum_ROI%'].round(2)
    result['Max_DD%'] = result['Max_DD%'].round(2)
    result['ROI/DD_Ratio'] = result['ROI/DD_Ratio'].round(2)

    # Print the DataFrame
    print("\nResulting DataFrame:")
    print(result)

    # Plot the data
    fig, ax = plt.subplots(figsize=(10, 6))

    # Plot Sum of ROI%
    ax.bar(result['DTE'], result['Sum_ROI%'], color='skyblue', edgecolor='black', label='Sum of ROI%', width=0.4, align='center')
    
    # Overlay Max DD (absolute values) on the same axis
    ax.plot(result['DTE'], result['Max_DD%'], color='red', marker='o', label='Max Drawdown (absolute)', linestyle='--', linewidth=2)

    ax.set_xlabel('DTE', fontsize=12)
    ax.set_ylabel('Values', fontsize=12)
    ax.tick_params(axis='x', rotation=45)

    # Title, legend, and grid
    plt.title('Sum of ROI%, Absolute Max Drawdown, and ROI/DD Ratio', fontsize=14)
    ax.legend(loc='upper left', fontsize=10)
    ax.grid(axis='y', linestyle='--', alpha=0.7)

    # Show the plot
    fig.tight_layout()
    plt.show()

plot_sum_roi_and_max_dd_by_dte(tb)


In [ ]:
def plot_sum_roi_and_max_dd_by_dte(tb):
    """
    Plots the sum of ROI% and Absolute Max Drawdown (Max DD) across all unique DTE values
    using a single Y-axis, and prints the resulting DataFrame.

    Parameters:
    tb (pd.DataFrame): Input DataFrame with 'DTE' and 'ROI%' columns.
    """
    # Ensure the DataFrame contains the required columns
    required_columns = {'DTE', 'ROI%'}
    if not required_columns.issubset(tb.columns):
        raise ValueError(f"Input DataFrame must contain columns: {required_columns}")
    
    # Group by DTE and calculate the sum of ROI%
    roi_result = tb.groupby('DTE', as_index=False)['ROI%'].sum()
    roi_result.rename(columns={'ROI%': 'Sum_ROI%'}, inplace=True)

    # Group by DTE and calculate Max DD (in absolute terms)
    dd_result = tb.groupby('DTE').apply(calculate_max_dd).reset_index()
    dd_result.rename(columns={0: 'Max_DD%'}, inplace=True)
    dd_result['Max_DD%'] = dd_result['Max_DD%'].abs()

    # Merge the sum of ROI% and Max DD data
    result = pd.merge(roi_result, dd_result, on='DTE')

    # Add ROI% / Max DD ratio
    result['ROI/DD_Ratio'] = result.apply(
        lambda row: row['Sum_ROI%'] / row['Max_DD%'] if row['Max_DD%'] != 0 else float('inf'), axis=1
    )

    # Format values
    result['Sum_ROI%'] = result['Sum_ROI%'].round(2)
    result['Max_DD%'] = result['Max_DD%'].round(2)
    result['ROI/DD_Ratio'] = result['ROI/DD_Ratio'].round(2)

    # Print the DataFrame
    print("\nResulting DataFrame:")
    print(result)

    # Plot the data
    fig, ax = plt.subplots(figsize=(10, 6))

    # Plot Sum of ROI%
    ax.bar(result['DTE'], result['Sum_ROI%'], color='skyblue', edgecolor='black', label='Sum of ROI%', width=0.4, align='center')
    
    # Overlay Max DD (absolute values) on the same axis
    ax.plot(result['DTE'], result['Max_DD%'], color='red', marker='o', label='Max Drawdown (absolute)', linestyle='--', linewidth=2)

    ax.set_xlabel('DTE', fontsize=12)
    ax.set_ylabel('Values', fontsize=12)
    ax.tick_params(axis='x', rotation=45)

    # Title, legend, and grid
    plt.title('Sum of ROI%, Absolute Max Drawdown, and ROI/DD Ratio', fontsize=14)
    ax.legend(loc='upper left', fontsize=10)
    ax.grid(axis='y', linestyle='--', alpha=0.7)

    # Show the plot
    fig.tight_layout()
    plt.show()

plot_sum_roi_and_max_dd_by_dte(tb)


In [25]:
# 3min TF
sorted_stats = {k: v for k, v in sorted(stats_dictionary.items(), key=lambda item: item[0], reverse=True)}
for x, y in sorted_stats.items():
    print(y.to_string())

        Total ROI Total Trades Win Rate Avg Profit% per Trade Avg Loss% per Trade Max Drawdown ROI/DD Ratio Variation
2019      85.9035           97  59.7938                3.3811             -2.8256     -12.1311       7.0813  48, 0.5%
2020     127.9911          118  57.6271                4.1027             -3.0198     -14.5938       8.7702  48, 0.5%
2021      89.5494          110  53.6364                4.2052             -3.1090     -20.1005       4.4551  48, 0.5%
2022     106.5603          106  59.4340                3.7684             -3.0430     -12.0577       8.8375  48, 0.5%
2023      44.0887          114  50.8772                3.4633             -2.7997     -20.6555       2.1345  48, 0.5%
2024      57.8441           75  56.0000                3.6423             -2.8828     -10.0489       5.7563  48, 0.5%
Overall  511.9372          620  56.1290                3.7772             -2.9504     -20.6555      24.7846  48, 0.5%
        Total ROI Total Trades Win Rate Avg Profit% per 

In [ ]:
df = pd.read_csv('')